# Open AI 연동

요약 -> 음성 읽어주기, 번역, linked 제공, 감성 분석

In [6]:
import gradio as gr
import requests
import uuid
import re

## 요약

In [7]:
########## GPT 호출 #########

def request_gpt(prompt):

    endpoint = gpt_endpoint

    # method : POST

    headers = {
        "Content-Type": "application/json",
        "api-key": gpt_key
    }

    body = {
        "messages": [
            {
            "role": "system",
            "content": [
                {
                "type": "text",
                "text": "너는 신문을 요약하여 주는 AI 도우미야. 100글자 이내로 영어로 번역해줘"
                }
            ]
            },
            {
            "role": "user",
            "content": [
                {
                "type": "text",
                "text": prompt
                }
            ]
            }

        ],
        "temperature": 0,
        "top_p": 0.95,
        "max_tokens": 800
    }

    response = requests.post(endpoint, headers = headers, json=body)
    print(response.status_code, response.content)

    if response.status_code == 200:

        response_json = response.json()
        message = response_json['choices'][0]['message']
        role = message['role']
        content = message['content']
        return content

    else:
        return ""


sample_prompt = "김광현은 지난 20일 20일 서울 롯데호텔월드에서 열린 ‘2025 신한 SOL Bank KBO 미디어데이&팬페스트’ 인터뷰에서 “(개막전 선발투수가 모두 외국인투수인 것이) 조금 아쉽다”라고 말했다. KBO리그는 오는 22일 정규시즌 개막전을 개최한다. 서울 잠실구장(LG-롯데), 대구 삼성라이온즈파크(삼성-키움), 인천 SSG랜더스필드(SSG-두산), 광주-기아 챔피언스필드(KIA-NC), 수원 KT위즈파크(KT-한화)에서 10개 구단이 144경기 대장정에 돌입한다.10개 구단은 미디어데이에서 모두 개막전 선발투수를 공개했다. LG 요니 치리노스, 롯데 찰리 반즈, 삼성 아리엘 후라도, 키움 케니 로젠버그, SSG 드류 앤더슨, 두산 콜 어빈, KIA 제임스 네일, NC 로건 앨런, KT 엔마누엘 데 헤이수스, 한화 코디 폰세가 개막전 선발투수로 나선다. 2017년 이후 8년 만에 전원 외국인투수다.김광현은 “예전에 나나 (류)현진이형(한화), (양)현종이(KIA) 같이 이제 베테랑에 접어든 선수들처럼 어린 선수들도 경험해보지 못하면 계속 못하는 것이다. 팀에서 그 정도 위치가 되는 선수들은 자신있게 1선발을 나가고 개막전에 나와야 앞으로도 더 경험을 쌓고 실력도 향상된다”라며 후배들이 개막전 선발투수로 나가지 못한 것을 아쉬워했다."
request_gpt(sample_prompt)

200 b'{"choices":[{"content_filter_results":{"hate":{"filtered":false,"severity":"safe"},"self_harm":{"filtered":false,"severity":"safe"},"sexual":{"filtered":false,"severity":"safe"},"violence":{"filtered":false,"severity":"safe"}},"finish_reason":"stop","index":0,"logprobs":null,"message":{"content":"Kim Kwang-hyun expressed regret that all Opening Day starters are foreign pitchers during an interview at the \'2025 Shinhan SOL Bank KBO Media Day \\u0026 Fan Fest\' on March 20.","refusal":null,"role":"assistant"}}],"created":1742540479,"id":"chatcmpl-BDQfX74AOcOZfHo9Ea6XqvraqeBjE","model":"gpt-4o-2024-11-20","object":"chat.completion","prompt_filter_results":[{"prompt_index":0,"content_filter_results":{"hate":{"filtered":false,"severity":"safe"},"self_harm":{"filtered":false,"severity":"safe"},"sexual":{"filtered":false,"severity":"safe"},"violence":{"filtered":false,"severity":"safe"}}}],"system_fingerprint":"fp_b705f0c291","usage":{"completion_tokens":41,"completion_tokens_details":

"Kim Kwang-hyun expressed regret that all Opening Day starters are foreign pitchers during an interview at the '2025 Shinhan SOL Bank KBO Media Day & Fan Fest' on March 20."

# 언어 감지

In [8]:
def request_language_detect(text_lan_detect=""):
    endpoint = endpoint_lan

    headers = {
        "Content-Type" : "application/json",
        "Ocp-Apim-Subscription-Key" : lan_key

    }
    
    request_id = str(uuid.uuid4())

    body = {
        "kind": "LanguageDetection",
        "parameters": {
            "modelVersion": "latest"
        },
        "analysisInput":{
            "documents":[
                {
                    "id": request_id,
                    "text": text_lan_detect
                }
            ]
        }
    }

    response = requests.post(endpoint, headers=headers, json=body)
    #print(response.status_code, response.content)

    if response.status_code == 200:
        response_json = response.json()
        language_code = response_json['results']['documents'][0]['detectedLanguage']['iso6391Name']

        if (language_code == "en" or language_code == "es"):
            print(language_code)
            return language_code
        
        else:
            return (f"지원하는 언어가 아닙니다. 언어는 {language_code}")

    else:
        return None

# 정보 링크 제공

In [9]:
def request_link(text, language="en"):

    
    endpoint = link_endpoint
    # method
    headers = {
        "Content-Type" : "application/json", 
        "Ocp-Apim-Subscription-Key" : link_key

    }

    request_id = str(uuid.uuid4())
    language = request_language_detect(text)

    body={
            "kind": "EntityLinking",
            "parameters": {
                "modelVersion": "latest"
            },
            "analysisInput":{
                "documents":[
                    {
                        "id":request_id,
                        "language":language,
                        "text": text
                    }
                ]
            }
    }

    response = requests.post(endpoint, headers = headers, json=body)
    print(response.status_code, response.content)

    response_json = response.json()
    entities = response_json['results']['documents'][0]['entities']

    # entity 받아오기
    #print('entities')
    # for entity in entities:
    #     entity_name = entity.get('name')  # 'name' 키의 값 가져오기
    #     entity_url = entity.get('url')    # 'url' 키의 값 가져오기
    #     print(f"Name: {entity_name}, URL: {entity_url}")


    return entities


request_link("Microsoft was founded by Bill Gates and Paul Allen on April 4, 1975.")

en
200 b'{"kind":"EntityLinkingResults","results":{"documents":[{"id":"2ba735b1-a7d3-4dc3-ae3e-ccdb988322e8","entities":[{"bingId":"a093e9b9-90f5-a3d5-c4b8-5855e1b01f85","name":"Microsoft","matches":[{"text":"Microsoft","offset":0,"length":9,"confidenceScore":0.48}],"language":"en","id":"Microsoft","url":"https://en.wikipedia.org/wiki/Microsoft","dataSource":"Wikipedia"},{"bingId":"0d47c987-0042-5576-15e8-97af601614fa","name":"Bill Gates","matches":[{"text":"Bill Gates","offset":25,"length":10,"confidenceScore":0.52}],"language":"en","id":"Bill Gates","url":"https://en.wikipedia.org/wiki/Bill_Gates","dataSource":"Wikipedia"},{"bingId":"df2c4376-9923-6a54-893f-2ee5a5badbc7","name":"Paul Allen","matches":[{"text":"Paul Allen","offset":40,"length":10,"confidenceScore":0.54}],"language":"en","id":"Paul Allen","url":"https://en.wikipedia.org/wiki/Paul_Allen","dataSource":"Wikipedia"},{"bingId":"52535f87-235e-b513-54fe-c03e4233ac6e","name":"April 4","matches":[{"text":"April 4","offset":54,"

[{'bingId': 'a093e9b9-90f5-a3d5-c4b8-5855e1b01f85',
  'name': 'Microsoft',
  'matches': [{'text': 'Microsoft',
    'offset': 0,
    'length': 9,
    'confidenceScore': 0.48}],
  'language': 'en',
  'id': 'Microsoft',
  'url': 'https://en.wikipedia.org/wiki/Microsoft',
  'dataSource': 'Wikipedia'},
 {'bingId': '0d47c987-0042-5576-15e8-97af601614fa',
  'name': 'Bill Gates',
  'matches': [{'text': 'Bill Gates',
    'offset': 25,
    'length': 10,
    'confidenceScore': 0.52}],
  'language': 'en',
  'id': 'Bill Gates',
  'url': 'https://en.wikipedia.org/wiki/Bill_Gates',
  'dataSource': 'Wikipedia'},
 {'bingId': 'df2c4376-9923-6a54-893f-2ee5a5badbc7',
  'name': 'Paul Allen',
  'matches': [{'text': 'Paul Allen',
    'offset': 40,
    'length': 10,
    'confidenceScore': 0.54}],
  'language': 'en',
  'id': 'Paul Allen',
  'url': 'https://en.wikipedia.org/wiki/Paul_Allen',
  'dataSource': 'Wikipedia'},
 {'bingId': '52535f87-235e-b513-54fe-c03e4233ac6e',
  'name': 'April 4',
  'matches': [{'te

# 음성 읽어주기 tts

In [10]:
def request_tts(text):
    file_name = "response_audio.wav"
    endpoint = tts_endpoint
    headers = {
        "Content-Type" : "application/ssml+xml",
        "X-Microsoft-OutputFormat" : "audio-16khz-128kbitrate-mono-mp3",
        "Ocp-Apim-Subscription-Key" : tts_key

    }
    body = f""" 
        <speak version='1.0' xml:lang='en-US'>
            <voice xml:lang='en-US' xml:gender='Female' name='en-US-AdamMultilingualNeural'>
                <prosody rate="20%">
                    {text}
                </prosody>
            </voice>
        </speak>
    """

    response = requests.post(endpoint, headers = headers, data=body)
    print(response.status_code, response.text)

    if response.status_code == 200:

        # 파일로 저장
        with open(file_name, 'wb') as audio_file:
            audio_file.write(response.content)
        return file_name

    else:
        return None
    

request_tts("Microsoft was founded by Bill Gates and Paul Allen on April 4, 1975.")

200 ����   H    LAME3.100UUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUULAME3.100UUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUU9�6v�;�8�8�z3L�1��5�0$"2=95̗3�Xq3�
��D����DY�D��D!�ٔe��y��Q�B��`��y�6fL���e�h��LP�a *d4����}L�``�Fdđ4e���C���3��� �V���00��ۑ%F|Y�^mK�hGQ�aU�FrufL!����ĵz� ��D2��0!�@qP�.�l�.5��h�[4n�ħ�0�F("PkU����*>\@'J�
� JӤYv|�= ��\i�[��۱eU.��Q5Af	Z6T����a�m��D0po; O� .XC�BH<M�k� ��T�h.��,!�P�Da�-=��[p^���8t!�8�Q����A
 [�ߤ�L*LAME3.100��������������������������������������������������������������������pl�vg�:t�Jf9�dF`�4h�fx�d��c
*d���
���R@ ���@�-�	�VY����
DLd)TY��� 1"C,Dy8X���9X� ��	�Z R°�������Ĳyl�]� ���I�		���T���h0`

'response_audio.wav'

# Gradio 화면 구현

gpt + tts

In [ ]:
with gr.Blocks() as demo:



    def click_send(text):
        file_path = request_tts(text)
        if file_path:
            return file_path
        else:
            return None
        
    def click_gpt_send(prompt, histories):
        content = request_gpt(prompt)
        histories.append({"role" : "user", "content" : prompt})
        if content:
            histories.append({"role" : "assistant", "content" : content})

        else: 
            error_message = "응답을 받지 못했습니다"
            histories.append({"role" : "assistant", "content" : error_message})
        
        # if content:
        #     histories.append((prompt, content))
        # else: 
        #     histories.append(( "assistant","응답을 받지 못했습니다"))

        return "", histories, content
    

    def change_chatbot(histories):
        history = histories[-1]
        content = history['content']
        pattern = r'[^가-힣a-zA-Z0-9\s]'
        cleaned_content = re.sub(pattern, '', content)
        
        audio_path = request_tts(cleaned_content)

        return audio_path
    


    gr.Markdown("# AI Speech World!")

    with gr.Row():

        # 좌측
        with gr.Column(scale = 4):
            chatbot = gr.Chatbot(type="messages")
            with gr.Row():
                prompt = gr.Textbox(label = "프롬포트", scale=6)
                send_gpt_button = gr.Button("전송", scale=1)
            
            #gpt_audio = gr.Audio(interactive=False, autoplay=False)
            

        # 우측
        with gr.Column(scale=1):

            with gr.Column():
                gr.Markdown("### TTS ###")

                tts_input_textbox = gr.Textbox(label="입력", placeholder="음성 변환할 텍스트를 입력하세요")
                send_tts_button = gr.Button('전송')

                output_tts_audio = gr.Audio(interactive=False, autoplay = True)


    send_tts_button.click(fn=click_send, inputs=[tts_input_textbox], outputs=[output_tts_audio])
    send_gpt_button.click(click_gpt_send, inputs=[prompt, chatbot], outputs=[prompt, chatbot, tts_input_textbox])
    chatbot.change(change_chatbot, inputs=[chatbot], outputs=[])

    demo.launch()

* Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.


/Users/parkjiyon/Desktop/MSAI6/GitHubConnect/Azure_OpenAI/openai/lib/python3.13/site-packages/gradio/blocks.py:1836: UserWarning: A function (change_chatbot) returned too many output values (needed: 0, returned: 1). Ignoring extra values.
    Output components:
        []
    Output values returned:
        ["response_audio.wav"]
  warnings.warn(


gpt + tts + link entity

In [ ]:


with gr.Blocks() as demo:
    def click_send(text):
        file_path = request_tts(text)
        if file_path:
            return file_path
        else:
            return None
    
    def click_gpt_send(prompt, histories):
        # GPT 응답 가져오기
        content = request_gpt(prompt)
        
        # 사용자 메시지를 히스토리에 추가
        histories.append({"role": "user", "content": prompt})
        
        # GPT 응답을 히스토리에 추가
        if content:
            histories.append({"role": "assistant", "content": content})
        else:
            error_message = "응답을 받지 못했습니다"
            histories.append({"role": "assistant", "content": error_message})
        
        # 링크 추출 요청
        try:
            links = request_link(prompt)
            links_text = "연관 링크:\n"
            for entity in links:
                entity_name = entity.get('name', '이름 없음')
                entity_url = entity.get('url', '#')
                links_text += f"- {entity_name}: {entity_url}\n"
        except Exception as e:
            links_text = f"링크 추출 중 오류 발생: {str(e)}"
        
        return "", histories, content, links_text
    
    def change_chatbot(histories):
        history = histories[-1]
        content = history['content']
        pattern = r'[^가-힣a-zA-Z0-9\s]'
        cleaned_content = re.sub(pattern, '', content)
        
        audio_path = request_tts(cleaned_content)
        return audio_path

    gr.Markdown("# AI Speech World!")
    
    with gr.Row():
        # 좌측
        with gr.Column(scale=4):
            chatbot = gr.Chatbot(type="messages")
            with gr.Row():
                prompt = gr.Textbox(label="프롬포트", scale=6)
                send_gpt_button = gr.Button("전송", scale=1)
            
            # 추출된 링크를 표시할 텍스트 영역
            links_output = gr.Textbox(label="연관 링크", lines=5)
        
        # 우측
        with gr.Column(scale=1):
            with gr.Column():
                gr.Markdown("### TTS ###")
                tts_input_textbox = gr.Textbox(label="입력", placeholder="음성 변환할 텍스트를 입력하세요")
                send_tts_button = gr.Button('전송')
                output_tts_audio = gr.Audio(interactive=False, autoplay=True)
    
    send_tts_button.click(fn=click_send, inputs=[tts_input_textbox], outputs=[output_tts_audio])
    
    # 전송 버튼 클릭 시 GPT 응답과 링크 추출 처리
    send_gpt_button.click(
        click_gpt_send, 
        inputs=[prompt, chatbot], 
        outputs=[prompt, chatbot, tts_input_textbox, links_output]
    )
    
    chatbot.change(change_chatbot, inputs=[chatbot], outputs=[])
    
demo.launch()

* Running on local URL:  http://127.0.0.1:7869

To create a public link, set `share=True` in `launch()`.


200 b'{"choices":[{"content_filter_results":{"hate":{"filtered":false,"severity":"safe"},"self_harm":{"filtered":false,"severity":"safe"},"sexual":{"filtered":false,"severity":"safe"},"violence":{"filtered":false,"severity":"safe"}},"finish_reason":"stop","index":0,"logprobs":null,"message":{"content":"Valencia deserves a match like this. Spain, aiming for the Nations League Final Four, drew 1-1 with the Netherlands after Merino\'s 93rd-minute goal.","refusal":null,"role":"assistant"}}],"created":1742543444,"id":"chatcmpl-BDRRM46lVpanpzmG3BnFJj89aIvCB","model":"gpt-4o-2024-11-20","object":"chat.completion","prompt_filter_results":[{"prompt_index":0,"content_filter_results":{"hate":{"filtered":false,"severity":"safe"},"self_harm":{"filtered":false,"severity":"safe"},"sexual":{"filtered":false,"severity":"safe"},"violence":{"filtered":false,"severity":"safe"}}}],"system_fingerprint":"fp_b705f0c291","usage":{"completion_tokens":37,"completion_tokens_details":{"accepted_prediction_tokens":

/Users/parkjiyon/Desktop/MSAI6/GitHubConnect/Azure_OpenAI/openai/lib/python3.13/site-packages/gradio/blocks.py:1836: UserWarning: A function (change_chatbot) returned too many output values (needed: 0, returned: 1). Ignoring extra values.
    Output components:
        []
    Output values returned:
        ["response_audio.wav"]
  warnings.warn(


200 ����   H    LAME3.100UUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUULAME3.100UUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUU�]�@h�	������a��N�c ���E?��Vc�A���M�	�P
 ��	~lL=c�E��!�D� �����_����<�pP��a��V���hPR���p�����ąn�4�p�پ	�!̂h�bND��Q^0�8� &a�q�BHNwy'Ď� �N#IEx"@P݇� �:^���J���&���z��p��c��q8���"x��x"ӔF�j`�	����q��=D����{�F2r+rUPuԘ�Nv�������L3Bu�[g@'H�g
vh26���N,<�O�}K�HAh�,`�ΧU"۫z!�e�M
·�&��d=��iC����-$p� ��EQ���P}�.�q���q��48P�W b�uSX k�n �ƌ`5��.��S��%�y�ᒪLAME3.100��������������������������������������������������������������������������������������������������������������_h�c�YM�B1���˃= �<�